# Model Test

In [1]:
MODELROOT = "/SSD2/bgkang/Chemomile/Model"
DATAROOT = "/SSD2/bgkang/Chemomile/"

modelpath = {
    'FP' : f"{MODELROOT}/FP-2024-07-17-02-08-03",
    'AIT' : f"{MODELROOT}/AIT-2024-07-17-02-21-21",
    'FLVL' : f"{MODELROOT}/FLVL-2024-07-17-02-25-23",
    'FLVU' : f"{MODELROOT}/FLVU-2024-07-17-02-29-19",
    'HCOM' : f"{MODELROOT}/HCOM-2024-07-17-04-48-42",
}

parameters = {
    'default' : dict(
        subfrag_size = 12,
        edge_size = 3,
        out_size = 1,
        seed = 42,
        batch_size = 128,
        max_epoch = 200,
        verbose = False,
        save = False,
    ),
    'FP' : dict(
        hidden_size = 64,
        dropout = 0.279,
        num_layers = 3,
        num_timesteps = 5,
        lr_init = 0.01,
        gamma = 0.978,
        weight_decay = 3.82E-3,
    ),
    'AIT' : dict(
        hidden_size = 128,
        dropout = 0.298,
        num_layers = 3,
        num_timesteps = 8,
        lr_init = 0.001,
        gamma = 0.982,
        weight_decay = 2.37E-4,
    ),
    'FLVL' : dict(
        hidden_size = 256,
        dropout = 0.238,
        num_layers = 4,
        num_timesteps = 5,
        lr_init = 0.0001,
        gamma = 0.979,
        weight_decay = 1.39E-2,
    ),
    'FLVU' : dict(
        hidden_size = 512,
        dropout = 0.268,
        num_layers = 6,
        num_timesteps = 6,
        lr_init = 0.0001,
        gamma = 0.979,
        weight_decay = 6.36E-2,
    ),
    'HCOM' : dict(
        hidden_size = 256,
        dropout = 0.276,
        num_layers = 7,
        num_timesteps = 4,
        lr_init = 0.0001,
        gamma = 0.986,
        weight_decay = 6.72E-3,
    ),
        
}

results = {
    'FP' : {
        'test' : {
            'true' : [],
            'pred' : [],
        },
        'total' : {
            'true' : [],
            'pred' : [],
        },
    },
    'AIT' : {
        'test' : {
            'true' : [],
            'pred' : [],
        },
        'total' : {
            'true' : [],
            'pred' : [],
        },
    },
    'FLVL' : {
        'test' : {
            'true' : [],
            'pred' : [],
        },
        'total' : {
            'true' : [],
            'pred' : [],
        },
    },
    'FLVU' : {
        'test' : {
            'true' : [],
            'pred' : [],
        },
        'total' : {
            'true' : [],
            'pred' : [],
        },
    },
    'HCOM' : {
        'test' : {
            'true' : [],
            'pred' : [],
        },
        'total' : {
            'true' : [],
            'pred' : [],
        },
    },
}

In [2]:
import sys
import torch
sys.path.append("/SSD2/bgkang/Chemomile")
from src.data import Dataset
from src.model import Chemomile
from src.train import Training

for key in results.keys():
    model = Chemomile(
        subfrag_size = parameters['default']['subfrag_size'],
        hidden_size = parameters[key]['hidden_size'],
        out_size = parameters['default']['out_size'],
        edge_size = parameters['default']['edge_size'],
        dropout = parameters[key]['dropout'],
        num_layers = parameters[key]['num_layers'],
        num_timesteps = parameters[key]['num_timesteps'],
    )
    model.load_state_dict(torch.load(modelpath[key]))

    dataset = Dataset(
        target = key,
        root = DATAROOT,
        seed = parameters['default']['seed'],
        batch_size = parameters['default']['batch_size'],
    )

    training = Training(
        model = model, 
        dataset = dataset, 
        parameters = parameters[key] | parameters['default'],
    )

    results[key]['test']['true'], results[key]['test']['pred'] = training.eval(total = False)
    results[key]['total']['true'], results[key]['total']['pred'] = training.eval(total = True)

print("All results are updated! >:D")

	DataDump found for 'FP'. Loading dumped data.
Training : 768 | Validation : 96 | Test : 96
Total : 960
	DataDump found for 'AIT'. Loading dumped data.
Training : 454 | Validation : 57 | Test : 57
Total : 568
	DataDump found for 'FLVL'. Loading dumped data.
Training : 375 | Validation : 47 | Test : 47
Total : 469
	DataDump found for 'FLVU'. Loading dumped data.
Training : 319 | Validation : 40 | Test : 40
Total : 399
	DataDump found for 'HCOM'. Loading dumped data.
Training : 727 | Validation : 91 | Test : 91
Total : 909
All results are updated! >:D


# Parity Plot

In [6]:
import matplotlib.pyplot as plt
import numpy as np
from sklearn.metrics import r2_score

COLORMAP = {
    'FP' : "#BF616A",
    'AIT' : "#5E81AC",
    'FLVL' : "#EBCB8B",
    'FLVU' : "#B48EAD",
    'HCOM' : "#A3BE8C",
}

def metric(true, pred):
    mae = np.abs(true - pred).mean()
    rmse = np.sqrt(np.power((true - pred), 2.0).mean())
    mape = np.abs((true - pred) / true * 100).mean()
    r2 = r2_score(true, pred)
    return mae, rmse, mape, r2
    

def beautifulTPPlot(top, bottom, key, unit):
    top.spines['top'].set_visible(False)
    top.spines['right'].set_visible(False)
    top.spines['left'].set_linewidth(5)
    top.spines['bottom'].set_linewidth(5)
    top.tick_params(axis = 'both', width = 5, length = 5, direction = 'in', labelsize = 30, pad = 10)
    top.set_xlabel("True %s (%s)" % (key, unit), fontsize = 30)
    top.set_ylabel("Predicted %s (%s)" % (key, unit), fontsize = 30)

    combined = np.stack([results[key]['total']['true'], results[key]['total']['pred']])

    top.plot(
        [combined.min(), combined.max()],
        [combined.min(), combined.max()],
        linestyle = '--', color = 'k', linewidth = 5)
    top.plot(
        results[key]['test']['true'],
        results[key]['test']['pred'],
        marker = 'o', markersize = 20, markeredgewidth = 5, markerfacecolor = "#FFFFFF", markeredgecolor = COLORMAP[key], linestyle = 'None', alpha = 0.8
    )
    top.annotate(
        "•MAE: %.03f\n•RMSE: %.03f\n•MAPE: %.03f\n•R$^2$: %.03f" % metric(results[key]['test']['true'], results[key]['test']['pred']),
        xy = (0.1, 0.7),
        xycoords = 'axes fraction',
        fontsize = 30,
        va = 'bottom'
    )
    
    bottom.spines['top'].set_visible(False)
    bottom.spines['right'].set_visible(False)
    bottom.spines['left'].set_linewidth(5)
    bottom.spines['bottom'].set_linewidth(5)
    bottom.tick_params(width = 5, length = 10, direction = 'in')
    bottom.tick_params(axis = 'both', width = 5, length = 5, direction = 'in', labelsize = 30, pad = 10)
    bottom.set_xlabel("True %s (%s)" % (key, unit), fontsize = 30)
    bottom.set_ylabel("Predicted %s (%s)" % (key, unit), fontsize = 30)
    
    bottom.plot(
        [combined.min(), combined.max()],
        [combined.min(), combined.max()],
        linestyle = '--', color = 'k', linewidth = 5)
    bottom.plot(
        results[key]['total']['true'],
        results[key]['total']['pred'],
        marker = 'o', markersize = 20, markeredgewidth = 5, markerfacecolor = "#FFFFFF", markeredgecolor = COLORMAP[key], linestyle = 'None', alpha = 0.8
    )
    bottom.annotate(
        "•MAE: %.03f\n•RMSE: %.03f\n•MAPE: %.03f\n•R$^2$: %.03f" % metric(results[key]['total']['true'], results[key]['total']['pred']),
        xy = (0.1, 0.7),
        xycoords = 'axes fraction',
        fontsize = 30,
        va = 'bottom',
    )

In [7]:
fig, ax = plt.subplots(2, 5, figsize = (48, 18), dpi = 300)

beautifulTPPlot(ax[0][0], ax[1][0], 'FP', 'K')
beautifulTPPlot(ax[0][1], ax[1][1], 'AIT', 'K')
beautifulTPPlot(ax[0][2], ax[1][2], 'HCOM', r'$\times$ 10$^3$ kJ mol$^{-1}$')
beautifulTPPlot(ax[0][3], ax[1][3], 'FLVL', "Vol % in air")
beautifulTPPlot(ax[0][4], ax[1][4], 'FLVU', "Vol % in air")

plt.tight_layout()
plt.savefig('Chemomile_Result.png', dpi = 300)
plt.show()